In [1]:
import json
import pandas as pd
import numpy as np
from pandas import json_normalize
import pytz
#from pandas.json_normalize import json_normalize

import os
import configparser
import datetime as dt
from datetime import datetime
from os.path import exists
from pandas_profiling import ProfileReport
import folium

# Method to read config file settings
def read_config(Config_File):
    config = configparser.ConfigParser()
    config.read(Config_File)
    return config

configurations = read_config("configurations.ini")

In [2]:
for each_section in configurations.sections():
    print("Section: {}".format(each_section))
    for (each_key, each_val) in configurations.items(each_section):
        print("key {} : Value {}".format(each_key,each_val))

Section: common_settings
key gtfs_history_data_root : Value C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data\GTFS-RT-historical-2022
key transitviewall_history_data_root : Value C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data	ransitviewall-historical-2022
key gtfs : Value C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data\gtfs_public_v202209020\google_bus


In [3]:
print(configurations['common_settings']['gtfs_history_data_root'])
print(configurations['common_settings']['transitviewall_history_data_root'])
print(configurations['common_settings']['GTFS'])

C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data\GTFS-RT-historical-2022
C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data	ransitviewall-historical-2022
C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data\gtfs_public_v202209020\google_bus


In [ ]:
#load 1 file in panda frame
month = '10'
day = '3'
hour = '14'
minute = '16'

file = configurations['common_settings']['gtfs_history_data_root'] + "\\" + month + '\\' + day + '\\' + hour + '\\' + minute + '\\' + 'feed.json'

with open(file) as json_file:
    data = json.load(json_file)
    #print(data['entity'])
from collections import Counter
c = Counter(entity['vehicle']['vehicle']['id'] for entity in data['entity'])
print(c)
# gtfs_rt_entities = json_normalize(data,errors='ignore', record_path=["entity"]
#                                                 ,meta=[["id"],
#                                                      ["vehicle","trip"]] )
# load json into flat dictionary
gtfs_rt_entities = json_normalize(data['entity'])
#gtfs_rt_entities['file'] = start_date_time # add the file date/time in the output
gtfs_rt_entities['in_service'] = [ 1 if isinstance(val, str) else 0 for val in gtfs_rt_entities['vehicle.trip.tripId']] # check if the vehicle is in service or not
gtfs_rt_entities.sort_index(axis=1, inplace=True)
# initial data cleaning, remove the vehicle that have not trip/route data
#gtfs_rt_entities = gtfs_rt_entities.dropna(subset = ['vehicle.trip.tripId'])
#gtfs_rt_entities.head(5)

#gtfs_rt_entities.to_csv('data\out.csv',index=False)

gtfs_rt_entities.head(5)

In [4]:
#TODO: create a parameter for file output
def load_gtfs_rt(start_date_time_str, stop_date_time_str):
    """ load GTFS RT file into a panda DF and store result to csv file"""
    start_date_time = datetime.strptime(start_date_time_str, '%m/%d/%Y %H:%M')
    stop_date_time = datetime.strptime(stop_date_time_str, '%m/%d/%Y %H:%M')
    
    # delta time
    delta = dt.timedelta(minutes=1)
    
    #initialize the file with header for dataframe
    with open('data\out.csv', 'w') as f:
        f.write('file,id,in_service,vehicle.currentStatus,vehicle.currentStopSequence,vehicle.position.bearing, \
            vehicle.position.latitude,vehicle.position.longitude,vehicle.position.speed,vehicle.stopId, \
            vehicle.timestamp,vehicle.trip.routeId,vehicle.trip.startDate,vehicle.trip.tripId,vehicle.vehicle.id,vehicle.vehicle.label')
        f.write("\n") # need to add the carriage return this way

    # iterate over range of date / time
    while (start_date_time <= stop_date_time):
        # print(start_date_time, end="\n")
        #generate the file name to open
        file = configurations['common_settings']['gtfs_history_data_root'] + "\\" \
            + start_date_time.strftime("%m") + '\\' \
            + start_date_time.strftime("%#d") + '\\' \
            + start_date_time.strftime("%H") + '\\' \
            + start_date_time.strftime("%M") + '\\' + 'feed.json'

        #load the file name into mem
        #TODO: if I don't find a file fail gracefully. print out the file not found.

        if exists(file):
            with open(file) as json_file:
                data = json.load(json_file)

            # load json into flat dictionary

            if "entity" in data:
                gtfs_rt_entities = json_normalize(data['entity'])
                gtfs_rt_entities['file'] = start_date_time # add the file date/time in the output
                gtfs_rt_entities['in_service'] = [ True if isinstance(val, str) else False for val in gtfs_rt_entities['vehicle.trip.tripId']] # check if the vehicle is in service or not
                gtfs_rt_entities['vehicle.timestamp'] = [datetime.fromtimestamp(int(val), pytz.timezone("UTC")) for val in gtfs_rt_entities['vehicle.timestamp']]
                gtfs_rt_entities.sort_index(axis=1, inplace=True) # sorting by column header to get consistant data between json files

            else:
                print("entity is key in not present in file {}".format(start_date_time))
            # initial data cleaning, remove the vehicle that have not trip/route data
            #gtfs_rt_entities = gtfs_rt_entities.dropna(subset = ['vehicle.trip.tripId'])

            # append the flatten data to csv file
            gtfs_rt_entities.to_csv('data\out.csv', mode='a', index=False, header=False)
        else:
            # if file is missing print a log
            print('file date/time not available: {}\\feed.json '.format(start_date_time.strftime("%m/%d/%Y %H:%M")))
        # increemnt datetime by 1 minute
        start_date_time += delta

        


In [ ]:
# start_Date_time_str = "10/3/2022 9:00"

# start_Date_time = datetime.strptime(start_Date_time_str, '%m/%d/%Y %H:%M')

load_gtfs_rt("10/03/2022 3:00","10/03/2022 23:59")

# print('shape {}'.format(gtfs_rt_entities.shape))

In [1]:
import numpy as np
import pandas as pd
from pandas_profiling import ProfileReport

df = pd.read_csv('data\out.csv')
profile = ProfileReport(df, title="GTFS RT Profiling Report")

c:\Users\AYAB\AppData\Local\Programs\Python\Python310\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
profile.to_widgets()

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
profile.to_notebook_iframe()

In [32]:
import json
import pandas as pd
#load 1 file in panda frame
month = '10'
day = '3'
hour = '14'
minute = '16'

file = r'C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data\transitviewall-historical-2022\\10\\3\\14\\16\\feed.json'
file_csv = r'C:\Users\AYAB\OneDrive - Drexel University\drexel\DSCI 591\detour project\data\transitviewall-historical-2022\\10\\3\\14\\16\\feed.csv'

with open(file,) as json_file:
    data = json.load(json_file)

# print(data['routes'])
# df = pd.DataFrame()
i = 0 
for routes in data['routes']:
    for route, buses_by_route_list in routes.items():
        # print(route)
        # print(buses)
        for bus_dict in buses_by_route_list:
            bus_dict['route'] = route # add the route number to each record
            # for key, value in bus_dict.items():
            #     print('{}->{}'.format(key,value))
            # df = df.append(bus_dict,ignore_index=True)
            head_row = ''
            row = ''
            for key, value in bus_dict.items():
                    head_row += str(key) + ','
                    row += str(value) + ','
                    
            if i == 0:
                with open (file_csv, 'w') as csv_file:
                            csv_file.write(head_row[:-1] + "\n")
                            csv_file.write(row[:-1]+ "\n")
                i = 1
            else:
                with open (file_csv, 'a') as csv_file:
                            csv_file.write(row[:-1]+ "\n")




# gtfs_rt_entities = json_normalize(data)


# gtfs_rt_entities.head(5)

(0, 0)


Empty DataFrame
Columns: []
Index: []

In [5]:
def Transform_transiviewall_in_csv(start_date_time_str, stop_date_time_str):
    start_date_time = datetime.strptime(start_date_time_str, '%m/%d/%Y %H:%M')
    stop_date_time = datetime.strptime(stop_date_time_str, '%m/%d/%Y %H:%M')

    while (start_date_time <= stop_date_time):
        # print(start_date_time, end="\n")
        #generate the file name to open
        file = configurations['common_settings']['transitviewall_history_data_root'] + "\\" \
            + start_date_time.strftime("%m") + '\\' \
            + start_date_time.strftime("%#d") + '\\' \
            + start_date_time.strftime("%H") + '\\' \
            + start_date_time.strftime("%M") + '\\' + 'feed.json'
        file_csv = configurations['common_settings']['transitviewall_history_data_root'] + "\\" \
            + start_date_time.strftime("%m") + '\\' \
            + start_date_time.strftime("%#d") + '\\' \
            + start_date_time.strftime("%H") + '\\' \
            + start_date_time.strftime("%M") + '\\' + 'feed.csv'
        #load the file name into mem
        #TODO: if I don't find a file fail gracefully. print out the file not found.
        
        delta = dt.timedelta(minutes=1)
        if exists(file):
            with open(file) as json_file:
                data = json.load(json_file)
            i = 0 
            for routes in data['routes']:
                for route, buses_by_route_list in routes.items():
                    # print(route)
                    # print(buses)
                    for bus_dict in buses_by_route_list:
                        bus_dict['route'] = route # add the route number to each record
                        # for key, value in bus_dict.items():
                        #     print('{}->{}'.format(key,value))
                        # df = df.append(bus_dict,ignore_index=True)
                        head_row = ''
                        row = ''
                        for key, value in bus_dict.items():
                                head_row += str(key) + ','
                                row += str(value) + ','
                                
                        if i == 0:
                            with open (file_csv, 'w') as csv_file:
                                        csv_file.write(head_row[:-1] + "\n")
                                        csv_file.write(row[:-1]+ "\n")
                            i = 1
                        else:
                            with open (file_csv, 'a') as csv_file:
                                        csv_file.write(row[:-1]+ "\n")
        # increemnt datetime by 1 minute
        start_date_time += delta

    

In [42]:
Transform_transiviewall_in_csv("10/03/2022 3:00","10/03/2022 23:59")

In [6]:
def load_transitviewall_csv(start_date_time_str, stop_date_time_str):
    start_date_time = datetime.strptime(start_date_time_str, '%m/%d/%Y %H:%M')
    stop_date_time = datetime.strptime(stop_date_time_str, '%m/%d/%Y %H:%M')

    delta = dt.timedelta(minutes=1) 
    data = pd.DataFrame
    i = 0
    while (start_date_time <= stop_date_time):
        # print(start_date_time, end="\n")
        #generate the file name to open
        file_csv = configurations['common_settings']['transitviewall_history_data_root'] + "\\" \
            + start_date_time.strftime("%m") + '\\' \
            + start_date_time.strftime("%#d") + '\\' \
            + start_date_time.strftime("%H") + '\\' \
            + start_date_time.strftime("%M") + '\\' + 'feed.csv'
        #load the file name into mem
        #TODO: if I don't find a file fail gracefully. print out the file not found.
        temp_data = pd.DataFrame
        delta = dt.timedelta(minutes=1)

        if exists(file_csv):
            temp_data = pd.read_csv(file_csv)
            if i == 0:
                data = temp_data
                i = 1
            else:
                frames = [data,temp_data]
                data = pd.concat(frames,axis=0,ignore_index=True)
        
        # increemnt datetime by 1 minute
        start_date_time += delta
    return data

In [8]:
data = load_transitviewall_csv("10/03/2022 3:00","10/03/2022 23:59")

print(data.head())
print(data.shape)




KeyboardInterrupt: 

In [9]:
profile2 = ProfileReport(data, title="TransitViewAll Profiling Report")

In [10]:
profile2.to_notebook_iframe()

NotImplementedError: 

In [11]:
print(data.columns)

In [31]:
def retreive_shape(trip_id):
    gtfs_shape_file = configurations['common_settings']['GTFS'] + "\\" + "shapes.txt"
    gtfs_trip_file = configurations['common_settings']['GTFS'] + "\\" + "trips.txt"

    trips = pd.read_csv(gtfs_trip_file)
    shapes = pd.read_csv(gtfs_shape_file)

    options = ['shape_id']

    filter_trip = trips[trips['trip_id'] == trip_id]
    shape_id = filter_trip.iloc[0]['shape_id']
    shape_by_trip_id = shapes[shapes['shape_id'] == shape_id]

    return shape_by_trip_id.sort_values(by=['shape_pt_sequence'])



In [33]:
data = retreive_shape(87166)
print(data)

        shape_id  shape_pt_lat  shape_pt_lon  shape_pt_sequence
101604    275145     39.996933    -75.235194                251
88899     275145     39.997303    -75.234802                252
246293    275145     39.997357    -75.234688                253
352390    275145     39.997530    -75.234325                254
428824    275145     39.997557    -75.234269                255
...          ...           ...           ...                ...
21192     275145     40.117885    -74.952325               1281
488090    275145     40.117851    -74.952572               1282
76232     275145     40.117590    -74.952844               1283
420408    275145     40.117361    -74.953048               1284
276299    275145     40.117252    -74.953034               1285

[1011 rows x 4 columns]
